In [27]:
import leafmap as leafmap
import leafmap.foliumap as leaf_folium
import leafmap.toolbar
# import leafmap.toolbar as toolbar

tmp_map = leafmap.Map()

Map = leaf_folium.Map()

url = "https://www.mrlc.gov/geoserver/mrlc_display/NLCD_2016_Land_Cover_L48/wms?"
Map.add_wms_layer(
    url,
    layers="NLCD_2016_Land_Cover_L48",
    name="NLCD 2016 CONUS Land Cover",
    format="image/png",
    transparent=True,
)
# Map.add_legend(builtin_legend="NLCD", draggable=False)
Map.sandbox_path = "/home/patel_zeel/bhuvan"
# toolbar.tool_template(Map)

Map.toolbar = tmp_map.toolbar
Map

In [1]:
from io import BytesIO
import requests

file_url = "https://drive.google.com/file/d/1fOujaaj_hJBMJIT-EsFzg6_6I-eFCgVs/view?usp=drivesdk"
if isinstance(file_url, str):
    if file_url.startswith("https://drive.google.com/file/d/"):
        ID = file_url.replace("https://drive.google.com/file/d/", "").split("/")[0]
        file_url = f"https://drive.google.com/uc?id={ID}"
    elif file_url.startswith("https://drive.google.com/open?id="):
        ID = file_url.replace("https://drive.google.com/open?id=", "")
        file_url = f"https://drive.google.com/uc?id={ID}"

    response = requests.get(file_url)
    bytes_data = BytesIO(response.content)
    string_data = response.text

In [2]:
import geopandas as gpd
import kml2geojson
if string_data.startswith("<?xml"):
    geojson = kml2geojson.convert(bytes_data)
    features = geojson[0]["features"]
    epsg = 4326
    input_gdf = gpd.GeoDataFrame.from_features(features, crs=f"EPSG:{epsg}")
else:
    input_gdf = gpd.read_file(bytes_data)

In [3]:
input_gdf

geometry             name  \
0                      POINT Z (73.90178 20.91581 0)                1   
1                      POINT Z (73.89839 20.91803 0)                3   
2                      POINT Z (73.89878 20.91578 0)                2   
3                      POINT Z (73.90075 20.91961 0)                4   
4  POLYGON Z ((73.89878 20.91579 0, 73.90179 20.9...  Polygon Measure   

         styleUrl  
0  #m_ylw-pushpin  
1  #m_ylw-pushpin  
2  #m_ylw-pushpin  
3  #m_ylw-pushpin  
4        #inline1

In [4]:
from shapely.ops import transform

def shape_3d_to_2d(shape):
    if shape.has_z:
        return transform(lambda x, y, z: (x, y), shape)
    else:
        return shape

def preprocess_gdf(gdf):
    gdf = gdf.to_crs(epsg=7761)  # epsg for Gujarat
    gdf["geometry"] = gdf["geometry"].apply(shape_3d_to_2d)
    gdf["geometry"] = gdf.buffer(0)  # Fixes some invalid geometries
    return gdf
input_gdf = preprocess_gdf(input_gdf)

In [5]:
input_gdf

geometry             name  \
0                                      POLYGON EMPTY                1   
1                                      POLYGON EMPTY                3   
2                                      POLYGON EMPTY                2   
3                                      POLYGON EMPTY                4   
4  POLYGON ((1262518.164 840333.056, 1262472.46 8...  Polygon Measure   

         styleUrl  
0  #m_ylw-pushpin  
1  #m_ylw-pushpin  
2  #m_ylw-pushpin  
3  #m_ylw-pushpin  
4        #inline1

In [6]:
def is_valid_polygon(geometry_gdf):
    geometry = geometry_gdf.geometry.item()
    return (geometry.type == "Polygon") and (not geometry.is_empty)

for i in range(len(input_gdf)):
    geometry_gdf = input_gdf[input_gdf.index == i]
    if is_valid_polygon(geometry_gdf):
        break

/tmp/ipykernel_850691/2543908025.py:3: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  return (geometry.type == "Polygon") and (not geometry.is_empty)
/tmp/ipykernel_850691/2543908025.py:3: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  return (geometry.type == "Polygon") and (not geometry.is_empty)
/tmp/ipykernel_850691/2543908025.py:3: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  return (geometry.type == "Polygon") and (not geometry.is_empty)
/tmp/ipykernel_850691/2543908025.py:3: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  return (geometry.type == "Polygon") and (not geometry.is_empty)


In [7]:
geometry_gdf

geometry             name  \
4  POLYGON ((1262518.164 840333.056, 1262472.46 8...  Polygon Measure   

   styleUrl  
4  #inline1

In [10]:
import pandas as pd
import geopandas as gpd
from tqdm.notebook import tqdm
from joblib import Parallel, delayed

In [12]:
files = """https://drive.google.com/open?id=1QHbcxHRw3EQWsw5-UN6AUnVI-bhmhCQ5
https://drive.google.com/open?id=1skBV8miaZN3gE2lPVnHQQG-n-RwbMH2d
https://drive.google.com/open?id=1jyG_D6UudyAgicZjsvEfNLT_vNK1G3EB
https://drive.google.com/open?id=1NxO399MvzufeT6-xigq3qi79psA40rkQ
https://drive.google.com/open?id=1P2ZPMsxX82P12m460EBjpYMrdXUkZ05l
https://drive.google.com/open?id=1Pc4sIYbRcu761fuXV5HVDG3EaqQC-uiz
https://drive.google.com/open?id=1xskOyh888HrxCrB0Ue9bNGG6r1CvlH3J
https://drive.google.com/open?id=12OJzdi0RE5BDdMHzBovnYK_QhC5jIiSy
https://drive.google.com/open?id=18bDqdNIZOlp97GHpEOaYsCLSTML--aEA
https://drive.google.com/open?id=1lge4nZKw7gxuDbQtM_v7D8eBHzUsLoBI
https://drive.google.com/open?id=1XzzPh1q0uU3eMPoSC5stCLC7r8oMtgok
https://drive.google.com/open?id=1JGmGCVYjdcUeFVmcoa7LcJE36HH0MGoF
https://drive.google.com/open?id=1EPp6DZUGFcUESQSeMjQ9famygnWM-3BM
https://drive.google.com/open?id=1XY7HbmY0fakAaZaxvUFF5UYk7Qovnit2
https://drive.google.com/open?id=1VSVOpw9TFAxPKClHGPFXI_anBSHZOIi-"""

df = pd.DataFrame(columns=['Failed URL', '# of geometries'])
i = 0
def get_gdf(link):
    link = link.strip()
    original_link = link
    if link.startswith('https://drive.google.com/open?id='):
        link = 'https://drive.google.com/uc?id=' + link.split('=')[-1]
    gdf = gpd.read_file(link)
    if len(gdf) != 1:
        print(f"{original_link} has {len(gdf)} geometries")
        # df.loc[i, ['Failed URL', '# of geometries']] = [original_link, len(gdf)]
        # i += 1
        
# df.to_csv('failed_links.csv', index=False)
_ = Parallel(n_jobs=32)(delayed(get_gdf)(link) for link in tqdm(files.split('\n')))

  0%|          | 0/15 [00:00<?, ?it/s]

https://drive.google.com/open?id=1skBV8miaZN3gE2lPVnHQQG-n-RwbMH2d has 5 geometries
https://drive.google.com/open?id=12OJzdi0RE5BDdMHzBovnYK_QhC5jIiSy has 6 geometries
https://drive.google.com/open?id=1lge4nZKw7gxuDbQtM_v7D8eBHzUsLoBI has 3 geometries
